In [28]:
import openai
import requests
import json
import re
import asyncio
import nest_asyncio
nest_asyncio.apply()

In [29]:
#Function to read text lines from a file

def read_text_file(file_name):
    with open(file_name, 'r') as file:
        return file.read().splitlines()

In [30]:
all_dialogues = read_text_file('data/friends_dataset.txt')

In [31]:
print(len(all_dialogues))

61338


In [32]:
OAI_API_BASE_URL = "http://localhost:8081/v1"
client = openai.OpenAI(
    base_url= OAI_API_BASE_URL,
    api_key = "sk-no-key-required"
)

In [48]:
async def query_oai_api(system_instruction,user_query, llm_anwer_start=''):
    completion = client.completions.create(
    model="llama2",
    prompt= f"[INST] <<SYS>>{system_instruction}<<SYS>> {user_query} [/INST] {llm_anwer_start}",
    )
    
    response = completion.choices[0]
    return response.text

In [34]:
def is_json(data):
    try:
        json.loads(data)
        return True
    except ValueError:
        return False

In [35]:
def get_json_qna(user_query, retries=3):
    
    for i in range(retries):
        try:
            response = query_oai_api(system_instruction,user_query)
            response = str(response)
            if is_json(response):
                return json.loads(response)
            else:
                match = re.search(r'`(.*?)`', response, re.S)
                if match and is_json(match.group(1)):
                    return json.loads(match.group(1)) 
                else:
                    raise Exception("Response is not a valid JSON")
        except Exception as e:
            print(f"Request failed: {e}")
            print(f"Attempt {i + 1} failed. Retrying...")
            continue
    print("Max retries exceeded. Skipping this chunk.")
    return None

In [103]:
async def process_dialogue_batch(system_instruction, dialogue_batch):
    print(dialogue_batch)
    return await query_oai_api(system_instruction=system_instruction, user_query=dialogue_batch, llm_anwer_start='Sure, here is the plot summary:')

In [104]:
def dump_to_file(data,file_name='myresults.txt'):
    with open(file_name, 'a') as file:
        data = data + '\n'
        file.write(data)

In [121]:
async def process_dialogues(batch_size=3):
    system_instruction = "You are an API that converts a conversation and into a short summary of the plot. Only give summary, no other text. Do this for the following conversation: \n\n"
    counter = 0
    dialouge_batches = [' '.join(all_dialogues[i:i + batch_size]) for i in range(0, len(all_dialogues), batch_size)]
    
    for dialogue_batch in dialouge_batches:
        counter += 1
        qna_task = process_dialogue_batch(system_instruction=system_instruction, dialogue_batch=dialogue_batch)
        tasks = [qna_task]
        results = await asyncio.gather(*tasks)

        for result in results:
            json_data = {'dialogues': dialogue_batch.strip('\n'), 'summary': result.strip('\n')}
            json_data = json.dumps(json_data)
            dump_to_file(json_data,file_name='summary_data.jsonl')
        
        #if counter == 3:
        #    break

In [122]:
 asyncio.run(process_dialogues(batch_size=10))

Monica Geller : There's nothing to tell! He's just some guy I work with! Joey Tribbiani : C'mon, you're going out with the guy! There's gotta be something wrong with him! Chandler Bing : All right Joey, be nice. So does he have a hump? A hump and a hairpiece? Phoebe Buffay : Wait, does he eat chalk? Phoebe Buffay : Just, 'cause, I don't want her to go through what I went through with Carl- oh! Monica Geller : Okay, everybody relax. This is not even a date. It's just two people going out to dinner and- not having sex. Chandler Bing : Sounds like a date to me. Chandler Bing : Alright, so I'm back in high school, I'm standing in the middle of the cafeteria, and I realize I am totally naked. #ALL# : Oh, yeah. Had that dream. Chandler Bing : Then I look down, and I realize there's a phone... there.
Joey Tribbiani : Instead of...? Chandler Bing : That's right. Joey Tribbiani : Never had that dream. Phoebe Buffay : No. Chandler Bing : All of a sudden, the phone starts to ring. Now I don't kno